
File: 06-lecture_solution.py


Michel Bierlaire

Thu Aug 22 12:02:56 2024



In [ ]:

import biogeme.biogeme_logging as blog
import numpy as np
from IPython.core.display_functions import display
from biogeme.biogeme import BIOGEME
from biogeme.expressions import Beta, log, exp, bioDraws, MonteCarlo
from biogeme.models import loglogit, logit
from biogeme.results import (
    bioResults,
    compile_estimation_results,
)


Variables used for the specification of the Swissmetro model are defined in the file `swissmetro_variables.py`.

In [ ]:
from swissmetro_variables import (
    database,
    CHOICE,
    TRAIN_AV_SP,
    SM_AV,
    CAR_AV_SP,
    TRAIN_TT_SCALED,
    TRAIN_COST_SCALED,
    TRAIN_HE_SCALED,
    SM_TT_SCALED,
    SM_COST_SCALED,
    SM_HE_SCALED,
    CAR_TT_SCALED,
    CAR_CO_SCALED,
)


As the estimation time may be long, we ask Biogeme to report the details of the iterations.

In [ ]:
logger = blog.get_screen_logger(level=blog.INFO)


**Tip:**<div class="alert alert-block alert-info">It is advised to start working with a low number of draws, until
the script is working well. Then, increase the number of draws to 10000, say.
Then, execute the script overnight.</div>

In [ ]:
number_of_draws = 10



# Parameters

In [ ]:
asc_car = Beta('asc_car', 0, None, None, 0)
asc_train = Beta('asc_train', 0, None, None, 0)
b_time = Beta('b_time', 0, None, None, 0)
b_cost = Beta('b_cost', 0, None, None, 0)
b_fr = Beta('b_fr', 0, None, None, 0)



# Availability conditions

In [ ]:
av = {1: TRAIN_AV_SP, 2: SM_AV, 3: CAR_AV_SP}



# Logit model

## Utility functions

In [ ]:
V1 = (
    asc_train
    + b_time * TRAIN_TT_SCALED
    + b_cost * TRAIN_COST_SCALED
    + b_fr * TRAIN_HE_SCALED
)
V2 = b_time * SM_TT_SCALED + b_cost * SM_COST_SCALED + b_fr * SM_HE_SCALED
V3 = asc_car + b_time * CAR_TT_SCALED + b_cost * CAR_CO_SCALED
V = {1: V1, 2: V2, 3: V3}



## Model

In [ ]:
logprob = loglogit(V, av, CHOICE)



## Estimation

In [ ]:
biogeme = BIOGEME(database, logprob)
biogeme.modelName = '01logit'
results_logit = biogeme.estimate(recycle=True)



## Results

General statistics

In [ ]:
print(results_logit.print_general_statistics())


Estimated parameters

In [ ]:
param_logit = results_logit.get_estimated_parameters()
display(param_logit)



# Random parameter: normal distribution

Read the results from file

In [ ]:
results_normal = bioResults(pickle_file='02normal.pickle')
param_normal = results_normal.get_estimated_parameters()
stats_normal = results_normal.get_general_statistics()



# Random parameter: lognormal distribution

In [ ]:
b_time_s = Beta('b_time_s', 1, None, None, 0)
b_time_rnd = -exp(b_time + b_time_s * bioDraws('b_time_rnd', 'NORMAL'))



## Utility functions

In [ ]:
V1 = (
    asc_train
    + b_time_rnd * TRAIN_TT_SCALED
    + b_cost * TRAIN_COST_SCALED
    + b_fr * TRAIN_HE_SCALED
)
V2 = b_time_rnd * SM_TT_SCALED + b_cost * SM_COST_SCALED + b_fr * SM_HE_SCALED
V3 = asc_car + b_time_rnd * CAR_TT_SCALED + b_cost * CAR_CO_SCALED
V = {1: V1, 2: V2, 3: V3}



## Model

In [ ]:
prob = logit(V, av, CHOICE)
logprob = log(MonteCarlo(prob))



## Estimation

In [ ]:
biogeme = BIOGEME(database, logprob, number_of_draws=number_of_draws)
biogeme.modelName = '03lognormal'
results_lognormal = biogeme.estimate()



## Results

General statistics

In [ ]:
stats_lognormal = results_lognormal.print_general_statistics()
print(stats_lognormal)


Estimated parameters

In [ ]:
param_lognormal = results_lognormal.get_estimated_parameters()
display(param_lognormal)



# Comparison

We build a summary data frame.

In [ ]:
summary = compile_estimation_results(
    {
        'Logit': results_logit,
        'Random param. (normal)': results_normal,
        'Random param. (lognormal)': results_lognormal,
    }
)
display(summary[0])


The values of `b_time`and `b_time_s` cannot be directly compared. Indeed, in the case of the log normal distribution,
they do not capture the mean and the standard deviation of the underlying distribution. We need to calculate them
explicitly.

In [ ]:
mean_normal = param_normal.at['b_time', 'Value']
stddev_normal = param_normal.at['b_time_s', 'Value']

location = param_lognormal.at['b_time', 'Value']
scale = param_lognormal.at['b_time_s', 'Value']
mean_lognormal = -np.exp(location + 0.5 * scale**2)
variance_lognormal = np.exp(2 * location + scale**2) * (np.exp(scale**2) - 1)
stddev_lognormal = np.sqrt(variance_lognormal)
print(f'Mean log normal: {mean_lognormal:.3g}')
print(f'Std. dev. log normal: {stddev_lognormal:.3g}')
print(f'Mean normal: {mean_normal:.3g}')
print(f'Std. dev. normal: {stddev_normal:.3g}')

The mean of the lognormal is more negative than the mean of the normal. Also, the standard deviation is larger.